<a href="https://colab.research.google.com/github/pascal-bergeron/ai4forgood2016/blob/main/DataVIZ_Julien_cleaned.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
import pandas as pd
import numpy as np

**Data visualisation**


In [2]:
from google.colab import files
# uploaded = files.upload()

In [3]:
from google.colab import drive
drive.mount('/content/drive/')

Mounted at /content/drive/


In [5]:
!pip install plotly==4.12.0

     |████████████████████████████████| 13.1MB 287kB/s 
  Found existing installation: plotly 4.4.1
    Uninstalling plotly-4.4.1:
      Successfully uninstalled plotly-4.4.1


In [6]:
import plotly.express as px

from urllib.request import urlopen
import json
with urlopen('http://donnees.ville.montreal.qc.ca/dataset/00bd85eb-23aa-4669-8f1b-ba9a000e3dd8/resource/e9b0f927-8f75-458c-8fda-b5da65cc8b73/download/limadmin.json') as response:
    arrondissements = json.load(response)


In [7]:
# Todo list
# Create a new Dataframe with all excel files merged together. - done
# Remove "Territoire à confirmer" and Total à Montréal. - done
# Match arrondisssements names between json and DF - done
# Add slider = DONE
# merge dates per week= DONE


In [8]:
# renaming dictionnary
di = {'Ahuntsic–Cartierville': 'Ahuntsic-Cartierville',
                       'Anjou':'Anjou',
                       "Baie-D'Urfé":"Baie-d'Urfé",
                       'Beaconsfield':'Beaconsfield',
                       'Côte-des-Neiges–Notre-Dame-de-Grâce':'Côte-des-Neiges-Notre-Dame-de-Grâce',
                       'Côte-Saint-Luc':'Côte-Saint-Luc',
                       'Dollard-des-Ormeaux':'Dollard-des-Ormeaux',
                        "Dorval":'Dorval',
                        "Hampstead":"Hampstead",
                        "Kirkland":'Kirkland',
                        "Lachine":"Lachine",
                        "LaSalle":'LaSalle',
                        "L'Île-Bizard–Sainte-Geneviève":"L'Île-Bizard-Sainte-Geneviève",
                        "Mercier–Hochelaga-Maisonneuve":'Mercier-Hochelaga-Maisonneuve',
                        "Montréal-Est":'Montréal-Est',
                        "Montréal-Nord":'Montréal-Nord',
                        "Montréal-Ouest":'Montréal-Ouest',
                        "Mont-Royal":'Mont-Royal',
                        "Outremont":'Outremont',
                        "Pierrefonds–Roxboro":'Pierrefonds-Roxboro',
                        "Plateau-Mont-Royal":'Le Plateau-Mont-Royal',
                        "Pointe-Claire":'Pointe-Claire',
                        "Rivière-des-Prairies–Pointe-aux-Trembles":'Rivière-des-Prairies-Pointe-aux-Trembles',
                        "Rosemont–La Petite Patrie":'Rosemont-La Petite-Patrie',
                        "Sainte-Anne-de-Bellevue":'Sainte-Anne-de-Bellevue',
                        "Saint-Laurent":'Saint-Laurent',
                        "Saint-Léonard": 'Saint-Léonard',
                        "Senneville": 'Senneville',
                        "Sud-Ouest":'Le Sud-Ouest',
                        "Verdun":'Verdun',
                        "Ville-Marie":'Ville-Marie',
                        "Villeray–Saint-Michel–Parc-Extension":'Villeray-Saint-Michel-Parc-Extension',
                        "Westmount":'Westmount'}

In [9]:
#Data wrangling function for daily covid report

def load_day(path,filename):
  # Load CSV
  df = pd.read_csv(path+filename,
                   dtype={"Arrondissements": str})
  # Add date column
  df['Date'] = filename[:-4]

  #Convert 'Cas confirmés' to INT
  df = df.replace('<5', )
  df["Cas Confirmés"] = pd.to_numeric(df["Cas Confirmés"])

  # Remove Extra lines
  df = df[df['Arrondissements'] != 'Territoire à confirmer']
  df = df[df['Arrondissements'] != 'Total à Montréal']

  # Convert date column to date time
  #df['Date']= pd.to_datetime(df['Date'])

  # Rename Arrondissements
  df.Arrondissements = df.Arrondissements.str.strip()
  df = df.replace({"Arrondissements": di})

  return df

#
#load_day(path,'2020-11-12.csv')

In [10]:
#Creates main Covid df from daily cvs reports

import os
from datetime import datetime

path = "/content/drive/My Drive/AIForGood2020/covid19-par-arrondissements-montreal/data/"

# Create empty Dataframe
df = pd.DataFrame()

# loop through the daily reports in a specific folder and append them to the main DF
for filename in os.listdir(path):
  # picks only Mondays reports. 
  if datetime.strptime(filename[:-4], '%Y-%m-%d').weekday() == 0:
    df = df.append(load_day(path,filename), ignore_index=True)


# Sort the main DF by date
df = df.sort_values(by=['Date'])

In [11]:
#a bit more renaming 

dic = {"L'Îe-Bizard-Sainte-Geneviève" : "L'Île-Bizard-Sainte-Geneviève",
       'Côte-des-Neiges-Notre-Dame-de-Grâce' : 'Côte-des-Neiges-Notre-Dame-de-Grâce',
       'Rivière-des-Prairies-Pointe-aux-Trembles' : 'Rivière-des-Prairies-Pointe-aux-Trembles',
       'Rosemont-La Petite Patrie' : 'Rosemont-La Petite-Patrie'}


df = df.replace({"Arrondissements": dic})

In [14]:
# Creates a choroplteth map with a weekly slider. 

fig = px.choropleth_mapbox(df, geojson=arrondissements, color='Cas Confirmés',
                           locations='Arrondissements', featureidkey="properties.NOM",
                           animation_frame='Date', #animation_group="Arrondissements",
                           center={"lat": 45.5517, "lon": -73.7073},
                           mapbox_style="carto-positron", zoom=9,
                           title='Progression des cas confirmés de Covid par arrondissements montréalais par semaine'
                           )

fig["layout"].pop("updatemenus") # optional, drop animation buttons

fig.update_layout(margin={"l":0,"b":0})

fig.show()

# fig = px.scatter(df, x="gdpPercap", y="lifeExp", animation_frame="year", animation_group="country",
#            size="pop", color="continent", hover_name="country",
#            log_x=True, size_max=55, range_x=[100,100000], range_y=[25,90])


# fig.show()

In [ ]:
#Downloads map as HTML file

import plotly.io as pio
pio.write_html(fig, file='covid_mtl.html', auto_open=True)

In [16]:
# Sunday Morning todo list

# Imports 211callsbyweek, add lat et lin column

# create dic with "Arrondissements, lat, lin,"


In [87]:
# calls = pd.read_csv('/content/drive/My Drive/AIForGood2020/211callsByWeek.csv',index_col=0)
# calls = calls.rename(columns={"year-week": "week","Municipalité_Nom":"Arrondissements"})
# calls["lat"] = ""
# calls['lin'] = ""
calls.dtypes

Arrondissements        object
week                   object
nbr_of_calls            int64
cumul_nbf_of_calls      int64
lat                   float64
long                  float64
dtype: object

In [117]:
calls = pd.read_csv('/content/drive/My Drive/AIForGood2020/covid19-par-arrondissements-montreal/test_points/211callsByWeek_final_1.csv',index_col=0,sep=";")
calls = calls.rename(columns={"year-week": "week","Municipalité_Nom":"Arrondissements"})
calls

Arrondissements        week  ...        lat       long
0    Ahuntsic-Cartierville  2020-04-06  ...  45.541465 -73.680496
1    Ahuntsic-Cartierville  2020-04-13  ...  45.541465 -73.680496
2    Ahuntsic-Cartierville  2020-04-20  ...  45.541465 -73.680496
3    Ahuntsic-Cartierville  2020-04-27  ...  45.541465 -73.680496
4    Ahuntsic-Cartierville  2020-05-04  ...  45.541465 -73.680496
..                     ...         ...  ...        ...        ...
800              Westmount  2020-08-10  ...  45.483244 -73.599472
801              Westmount  2020-08-17  ...  45.483244 -73.599472
802              Westmount  2020-08-24  ...  45.483244 -73.599472
803              Westmount  2020-08-31  ...  45.483244 -73.599472
804              Westmount  2020-09-07  ...  45.483244 -73.599472

[759 rows x 6 columns]

In [118]:
#Bubble chart example

import plotly.express as px
#df_temp = px.data.gapminder()

fig = px.scatter_mapbox(calls, lat="lat", lon="long",
	         size="cumul_nbf_of_calls", #color="continent",
           animation_frame="week", animation_group='Arrondissements',
            hover_name="cumul_nbf_of_calls", #size_max=50
            hover_data=['Arrondissements',"cumul_nbf_of_calls"],
            center={"lat": 45.5517, "lon": -73.7073},
            title='Progression des appels au 211 par arrondissements montréalais par semaine pendant Covid'
            )
fig.update_layout(mapbox_style="carto-positron")
fig.show()

In [120]:
import plotly.io as pio
pio.write_html(fig, file='211_mtl_final.html', auto_open=True)

In [ ]:
# fig = px.choropleth_mapbox(df, geojson=arrondissements, color='Cas Confirmés',
#                            locations='Arrondissements', featureidkey="properties.NOM",
#                            animation_frame='Date', #animation_group="Arrondissements",
#                            center={"lat": 45.5517, "lon": -73.7073},
#                            mapbox_style="carto-positron", zoom=9,
#                            title='Progression des cas confirmés de Covid par arrondissements montréalais par semaine'
#                            )

# #Bubble chart example

# import plotly.express as px
# #df_temp = px.data.gapminder()

# fig = px.scatter_mapbox(calls, lat="lat", lon="long",
# 	         size="cumul_nbf_of_calls", #color="continent",
#            animation_frame="week", animation_group='Arrondissements',
#             hover_name="cumul_nbf_of_calls", #size_max=50
#             )
# fig.update_layout(mapbox_style="carto-positron")
# fig.show()


# fig.show()

import plotly.graph_objects as go



data = [
px.choropleth_mapbox(df, geojson=arrondissements, color='Cas Confirmés',
                           locations='Arrondissements', featureidkey="properties.NOM",
                           animation_frame='Date', #animation_group="Arrondissements",
                           #center={"lat": 45.5517, "lon": -73.7073},
                           mapbox_style="carto-positron", zoom=9,
                           title='Progression des cas confirmés de Covid par arrondissements montréalais par semaine'
                           ),

px.scatter_mapbox(calls, lat="lat", lon="long",
	         size="cumul_nbf_of_calls", #color="continent",
           animation_frame="week", animation_group='Arrondissements',
            hover_name="cumul_nbf_of_calls", #size_max=50
            )

]

fig = go.Figure(data=data)

fig["layout"].pop("updatemenus") # optional, drop animation buttons
fig.update_layout(margin={"l":0,"b":0})

fig.show()

#iplot(fig, filename='Multiple Mapbox')


In [102]:
#centroid = (sum(lon) / len(lon), sum(lat) / len(lat))